### Learn new skills from resumes

Data has been taken from Dataturks Repoistory which contains 220 annotated resumes Entity Recognition In Resumes Data

For this challenge, we are learning New Skills from Resumes
Parsing resumes and extracting information is good, but learning new skills from resume is important for any hiring organisation, since skills keep evolving over time and very often candidates miss out to add skills relevant to their experience. So, automatically learning new skills is vital for both candidates and hiring team.

The keys fields in this dataset are: content - text from resume, annotations - includes important labels like Name, Organisation, Skills etc.

Source: https://github.com/rajkstats/Learning_new_skills_from_resume/blob/master/Cutshort_Data_Challenge-Resumes_NER.ipynb

In [5]:
import pandas as pd
from collections import Counter
import spacy,re,json
from spacy.gold import GoldParse
from spacy.scorer import Scorer
from spacy import displacy  

from sklearn.metrics import classification_report
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import accuracy_score

import warnings
warnings.filterwarnings('ignore')

from __future__ import unicode_literals, print_function
import plac
import random
from pathlib import Path
import spacy
from spacy.util import minibatch, compounding

PATH ='data/Resumes.json'

with open(PATH, 'r') as f:
    lines = f.readlines()
df=[]
for line in lines:
    data = json.loads(line)
    df.append(data)
    
df=pd.DataFrame(df)
df.head(5)

content  \
0  Abhishek Jha\nApplication Development Associat...   
1  Afreen Jamadar\nActive member of IIIT Committe...   
2  Akhil Yadav Polemaina\nHyderabad, Telangana - ...   
3  Alok Khandai\nOperational Analyst (SQL DBA) En...   
4  Ananya Chavan\nlecturer - oracle tutorials\n\n...   

                                          annotation extras  
0  [{'label': ['Skills'], 'points': [{'start': 12...   None  
1  [{'label': ['Email Address'], 'points': [{'sta...   None  
2  [{'label': ['Skills'], 'points': [{'start': 37...   None  
3  [{'label': ['Skills'], 'points': [{'start': 80...   None  
4  [{'label': ['Degree'], 'points': [{'start': 20...   None

In [2]:
!python -m spacy download en_core_web_sm

/Users/majiga/anaconda3/bin/python: No module named spacy.__main__; 'spacy' is a package and cannot be directly executed


In [34]:
# Number of Rows and columns
print(df.shape)

# Finding all the unique labels in training data
uniq_labels=[]
for lines in df['annotation']:
    u = str(lines[0]['label']).strip('[]')
    uniq_labels.append(u)
    
set(uniq_labels)

(220, 3)


{'',
 "'College Name'",
 "'Companies worked at'",
 "'Degree'",
 "'Designation'",
 "'Email Address'",
 "'Graduation Year'",
 "'Location'",
 "'Name'",
 "'Skills'",
 "'Years of Experience'"}

In [39]:
# Finding all the unique skills in data
uniq_skills=[]
for lines in df['annotation']:
    u = str(lines[0]['label']).strip('[\'\']')
    if u == 'Skills':
        for skill in lines[0]['points']:
            l = skill['text'].strip('\n')
            uniq_skills.append(l.strip())
print('Unique skills = ', len(uniq_skills), *set(uniq_skills), sep='\n')

Unique skills = 
132
Jira, Ansible, Jenkins, Splunk, Nagios, Docker, Python, AWS, Bamboo, Linux, Git, Chef, Windows,
Powershell Scripting
CHEF
Skills: JAVA, C#, WPF, XAML, Robot Framework, Scrum, Guice, ATDD, SOA, Fixed Income, CoreNLP,
SOLID
programming, OOPs, NLP, Microservice architecture.
Splunk, Network Security, Arc sight (2 years), SIEM (2 years), McAfee ESM (1 year)
Application Development, Software Testing
REST
Languages Java, Java Script, PL/SQL, SQL SERVER, HTML, XML,
XSLT
Application Servers J Boss, Apache Tomcat, Web logic, IBM web sphere

Databases Oracle, SQL SERVER

Development Tools MVC, Singleton, Session Facade, DTO, DAO,

Service Locator

SOA Restful Web Service, Soap web service, JAX-RS, XML, JSON, WS
Security, Mule ESB

IDE's/TOOLS Eclipse, Mule Anypoint Studio

Java/J2EETechnologies Java, Servlets, JSP, JDBC, EJB, JMS

Protocols HTTP, FTP, TCP/IP

Version Control tools CVS, SVN, GIT

Build Tool Ant, Maven

Bug Tracking Tools HP Quality Center, Rally

Frameworks S

In [22]:
PATH ='data/Resumes.json'

with open(PATH, 'r') as f:
    lines = f.readlines()
d=[]
for line in lines:
    data = json.loads(line)
    text = data['content']
    d.append(text.replace('\n', ' '))
    
d=pd.DataFrame(d)
d.to_csv('data/annotate_resume.csv',index=False)

In [52]:
# Annotating guideline is to label individual skills appearing in content of resume anywhere not just in skills section
# and avoiding punctuations and nextline character.
# The keys fields in annotated data are:
# id - serial number given by doccano annotator tool
# text - content of resumes
# meta - no meta
# annotation approver - null in our case
# label - skills which are annotated in each resumes content
# Credit for thsi annotated dataset of skills: https://github.com/rajkstats/Learning_new_skills_from_resume
PATH ='data/ner.json1'

annotated_data = []
lines=[]
with open(PATH, 'r') as f:
    lines = f.readlines()
print(len(lines))

unique_skills_train_ds = {}

for line in lines:
    data = json.loads(line)
    text = data['text']
    entities = []
    for label in data['labels']:
        entities.append(label)
        #print(label, text[label[0]:label[1]])
        skill = text[label[0]:label[1]].strip()
        unique_skills_train_ds[skill] = 1
    annotated_data.append((text, {"entities": data['labels']}))

print('Number of unique_skills_train_ds = ', len(unique_skills_train_ds), *sorted(unique_skills_train_ds.keys()), sep='\n')
print(annotated_data[0])

220
Number of unique_skills_train_ds = 
1003
.NET
.Net
.Net 4.5
.net
.net API
ABAP
ABAP/4
ACCEPTANCE TESTING
ACCESS
ACTIVE DIRECTORY
ADBC
ADF
ADO.Net
ADOBE PHOTOSHOP
AJAX
ALGORITHMS
ALM
ALSA
AMADEUS
AMDOCS
ANALOG
ANDROID
ANSYS
AP
APACHE HADOOP HDFS
APACHE KAFKA
APEX
API
API Testing
APM
APPLICATION SOFTWARE
APPRAISAL
APS
AR
ARCHITECTURE
ASP
ASP Tool
ASP.NET
ASP.Net
ASP.Net MVC
ATDD
AUDITING
AUTOCAD
AWS
AWS API
AWS Elastic Map reduce
AWS python SDK
AWS redshift
Access
Accounts Payable-FI-A/P
Accounts Receivable FI-A/R
Active Directory
Adobe Flex
Adobe Photoshop
Advanced  SQL
Advanced Excel
Agile
Agile Methodologies
Agile Methodology
Agile planning
Ajax
Amazon Elastic Block Storage
Amazon Elastic Compute Cloud
Analytics
Android
Android Studio
Angular JS
Angular Js
AngularJS
AngularJs
Angularjs
Ansible
Ansys
Ant
Apache
Apache Nifi
AppDynamics
Application Development
Application Manager
Arc sight
Architecture
Ariba 1.5
Artifactory
Artificial Intelligence
Asp.Net
Asp.net
Audit
Auditing
Autom

In [24]:
# We have trained 220 resumes for skills , now we will train our model on 200 resumes and test on 20 resumes.
training_data=  annotated_data[0:200]
test_data = annotated_data[200:220]
print(len(training_data), len(test_data))

200 20


In [27]:
# train the model on 200 annotated resumes with 100 iterations to train our model and use the saved model for predictions
def main(model=None, output_dir=None, n_iter=100):
    """Load the model, set up the pipeline and train the entity recognizer."""
    if model is not None:
        nlp = spacy.load(model)  # load existing spaCy model
        print("Loaded model '%s'" % model)
    else:
        nlp = spacy.blank("en")  # create blank Language class
        print("Created blank 'en' model")

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if "ner" not in nlp.pipe_names:
        ner = nlp.create_pipe("ner")
        nlp.add_pipe(ner, last=True)
    # otherwise, get it so we can add labels
    else:
        ner = nlp.get_pipe("ner")

    # add labels
    for _, annotations in training_data:
        for ent in annotations.get("entities"):
            ner.add_label(ent[2])

    # get names of other pipes to disable them during training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != "ner"]
    with nlp.disable_pipes(*other_pipes):  # only train NER
        # reset and initialize the weights randomly – but only if we're
        # training a new model
        if model is None:
            nlp.begin_training()
        for itn in range(n_iter):
            random.shuffle(training_data)
            losses = {}
            # batch up the examples using spaCy's minibatch
            batches = minibatch(training_data, size=compounding(4.0, 32.0, 1.001))
            for batch in batches:
                texts, annotations = zip(*batch)
                nlp.update(
                    texts,  # batch of texts
                    annotations,  # batch of annotations
                    drop=0.5,  # dropout - make it harder to memorise data
                    losses=losses,
                )
            print("Losses", losses)

    # test the trained model
    for text, _ in training_data:
        doc = nlp(text)
        print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
        print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])

    # save model to output directory
    if output_dir is not None:
        output_dir = Path(output_dir)
        if not output_dir.exists():
            output_dir.mkdir()
        nlp.to_disk(output_dir)
        print("Saved model to", output_dir)

        # test the saved model
        print("Loading from", output_dir)
        nlp2 = spacy.load(output_dir)
        for text, _ in training_data:
            doc = nlp2(text)
            print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
            print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])

# trained this model with 100 iterations in google colab using GPU runtime with loss: Losses {'ner': 465.24571515528373} 
main(output_dir='model/ner_model/')

Created blank 'en' model
Losses {'ner': 15225.528229114978}
Losses {'ner': 2840.4249927861365}
Losses {'ner': 2795.0841199045517}
Losses {'ner': 2654.6868951894185}
Losses {'ner': 2656.0819350406264}
Losses {'ner': 2521.0158029963495}
Losses {'ner': 2277.6671058094907}
Losses {'ner': 2141.3671469278056}
Losses {'ner': 2151.3800267467695}
Losses {'ner': 2076.7369840394567}
Losses {'ner': 1946.7929016911244}
Losses {'ner': 1934.7435846951216}
Losses {'ner': 1779.8449827509553}
Losses {'ner': 1663.7067355109875}
Losses {'ner': 1803.716115592211}
Losses {'ner': 2145.175933361346}
Losses {'ner': 1664.7308511989584}
Losses {'ner': 1602.6743082561961}
Losses {'ner': 1603.6105449844667}
Losses {'ner': 1497.1872345018437}
Losses {'ner': 1257.225231122441}
Losses {'ner': 1380.7976073808807}
Losses {'ner': 1265.2613825587978}
Losses {'ner': 1311.418930634935}
Losses {'ner': 1279.1710781778404}
Losses {'ner': 1145.7383984160324}
Losses {'ner': 1298.5877940752737}
Losses {'ner': 1177.352142370249}


In [31]:
# In the resume content, skill KERAS is added, not seen during labeling. Let's see if our model can learn this as new skill
test_text = '"Abhishek Jha Application Development Associate - Accenture  Bengaluru, Karnataka - Email me on Indeed: indeed.com/r/Abhishek-Jha/10e7a8cb732bc43a  • To work for an organization which provides me the opportunity to improve my skills and knowledge for my individual and company\'s growth in best possible ways.  Willing to relocate to: Bangalore, Karnataka  WORK EXPERIENCE  Application Development Associate  Accenture -  November 2017 to Present  Role: Currently working on Chat-bot. Develop Keras models for the Bot which will be triggered based on given input. Also, Training the bot for different possible utterances (Both positive and negative), which will be given as input by the user.  EDUCATION  B.E in Information science and engineering  B.v.b college of engineering and technology -  Hubli, Karnataka  August 2013 to June 2017  12th in Mathematics  Woodbine modern school  April 2011 to March 2013  10th  Kendriya Vidyalaya  April 2001 to March 2011  SKILLS  KERAS (Less than 1 year), Database (Less than 1 year), Database Management (Less than 1 year), Database Management System (Less than 1 year), Java (Less than 1 year)  ADDITIONAL INFORMATION  Technical Skills  https://www.indeed.com/r/Abhishek-Jha/10e7a8cb732bc43a?isid=rex-download&ikw=download-top&co=IN   • Programming language: C, C++, Java • Oracle PeopleSoft • Internet Of Things • Machine Learning • Database Management System • Computer Networks • Operating System worked on: Linux, Windows, Mac  Non - Technical Skills  • Honest and Hard-Working • Tolerant and Flexible to Different Situations • Polite and Calm • Team-Player"'

In [33]:
nlp = spacy.load('model/ner_model/')
doc_text=nlp(test_text)
displacy.render(doc_text, style="ent", jupyter=True)

### Evaluation
- Testing the trained model on 20 test annotated resumes which were not seen by model during training
- Model can be deployed on cloud providers like AWS

In [30]:
nlp = spacy.load('model/ner_model/')  

tp=0
tr=0
tf=0

ta=0
c=0        
for text,annot in test_data:
    f=open("resume"+str(c)+".txt","w")
    doc_to_test=nlp(text)
    d={}
    for ent in doc_to_test.ents:
        d[ent.label_]=[]
    for ent in doc_to_test.ents:
        d[ent.label_].append(ent.text)

    for i in set(d.keys()):
        f.write("\n\n")
        f.write(i +":"+"\n")
        for j in set(d[i]):
            f.write(j.replace('\n','')+"\n")
    d={}
    for ent in doc_to_test.ents:
        #print(ent)
        d[ent.label_]=[0,0,0,0,0,0]
    for ent in doc_to_test.ents:
        doc_gold_text= nlp.make_doc(text)
        gold = GoldParse(doc_gold_text, entities=annot.get("entities"))
        y_true = [ent.label_ if ent.label_ in x else 'Not '+ent.label_ for x in gold.ner]
        y_pred = [x.ent_type_ if x.ent_type_ ==ent.label_ else 'Not '+ent.label_ for x in doc_to_test]  
        if(d[ent.label_][0]==0):
            (p,r,f,s)= precision_recall_fscore_support(y_true,y_pred,average='weighted')
            a=accuracy_score(y_true,y_pred)
            d[ent.label_][0]=1
            d[ent.label_][1]+=p
            d[ent.label_][2]+=r
            d[ent.label_][3]+=f
            d[ent.label_][4]+=a
            d[ent.label_][5]+=1
    c+=1
for i in d:
    print("\n For Entity "+i+"\n")
    print("Accuracy : "+str((d[i][4]/d[i][5])*100)+"%")
    print("Precision : "+str(d[i][1]/d[i][5]))
    print("Recall : "+str(d[i][2]/d[i][5]))
    print("F-score : "+str(d[i][3]/d[i][5]))


 For Entity Skills

Accuracy : 98.77300613496932%
Precision : 0.9878815420737711
Recall : 0.9877300613496932
F-score : 0.9847006820866516


In [56]:
unique_skills_text_ds = {}
for text, _ in test_data:
    doc = nlp(text)
    for ent in doc.ents:
        unique_skills_text_ds[ent.text] = 1
print('Number of unique_skills_text_ds = ', len(unique_skills_text_ds))
print(*sorted(unique_skills_text_ds.keys()), sep='\n')

Number of unique_skills_text_ds =  74
4
5
ASP.NET 3.5
AUDITING
Ajax
Asp.Net
Auditing
Azure
BMC Remedy Support
C
C#
C++
CFA
CSS
CSS3
DATA BACKUP
DERIVATIVES
Data management
EXCEL
EXCHANGE
Excel
HTML
HTML5
INCIDENT MANAGEMENT
IT INFRASTRUCTURE
IT consultancy
Java
JavaScript
JavaScript/jQuery
Javascript
LAN
Linux
MAINTENANCE
MS OFFICE
MS Office
MS-Access
Microsoft Azure
Microsoft Office
Microsoft Office 2007
Microsoft Windows
Microsoft service now
Network &
Network management
Operations
PL/SQL
POWERPOINT
Personal Assistant
Power Point
PowerPoint
Project management
SAP
SAP BI
SAP HANA
SAP database server
SIEM
SQL
SQL Server
Server Management
Software Solution
Software management
Splunk
Sql server
TALLY
Unix
VBA
Web Development
Web server
Windows
Windows 7
Windows NT
Windows server
Word
vendor development
vendor management


In [61]:
new_skills_found = unique_skills_text_ds.keys() - unique_skills_train_ds.keys()
print('Number of new skills in test dataset = ', len(new_skills_found), new_skills_found)

Number of new skills in test dataset =  24 {'Microsoft Office 2007', 'Microsoft Windows', 'Windows server', 'vendor development', 'JavaScript/jQuery', 'Microsoft Azure', 'Windows NT', 'Server Management', 'IT consultancy', 'Windows 7', 'Data management', 'vendor management', 'Software management', 'Web server', 'Personal Assistant', '5', 'Network management', 'Network &', 'Software Solution', 'ASP.NET 3.5', 'BMC Remedy Support', '4', 'SAP database server', 'Microsoft service now'}
